In [87]:
# Импортируем необходимые библиотеки
import datetime
import numpy as np
import scipy as sp
import pandas as pd
import lightgbm as lgb
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import OneHotEncoder

## Часть 1. Подготовка данных

In [182]:
# Импортируем данные
df_raw = pd.read_csv('/Users/alexeysek/Desktop/SAS/HW2_SAS/hw2_train.csv', index_col=0)
store_location = pd.read_csv('/Users/alexeysek/Desktop/SAS/HW2_SAS/STORE_LOCATION.csv', sep=';')

df_raw['period_start_dt'] = pd.to_datetime(df_raw['period_start_dt'])

In [183]:
# Добавим такие признаки, как день, месяц, год
df_raw['day'] = df_raw['period_start_dt'].dt.day
df_raw['month'] = df_raw['period_start_dt'].dt.month
df_raw['year'] = df_raw['period_start_dt'].dt.year
# Также добавим день недели и номер недели
df_raw['weekday'] = df_raw['period_start_dt'].dt.dayofweek
df_raw['weeknum'] = df_raw['period_start_dt'].dt.isocalendar().week

In [184]:
# Посмотрим на данные по магазинам
store_location

STORE_LOCATION_RK  STORE_LOCATION_LVL_RK4  STORE_LOCATION_LVL_RK3  \
0                   277                     124                     124   
1                   278                     124                     124   
2                   279                     183                     183   
3                   280                     211                     211   
4                   281                     221                     221   
5                   282                     201                     201   
6                   283                     197                     197   
7                   284                     228                     228   
8                   285                     222                     222   
9                   286                     230                     230   
10                  287                     220                     220   
11                  288                     211                     211   
12                  289                     124                     124   
13                  290                     186                     186   
14                  291                     211                     211   
15                  292                     233                     233   
16                  293                     234                     234   
17                  294                     163                     163   
18                  295                     235                     235   
19                  296                     124                     124   
20                  297                     236                     236   
21                  298                     238                     238   
22                  299                     124                     124   
23                  300                     210                     210   
24                  301                     215                     215   
25                  302                     240                     240   
26                  303                     237                     237   
27                  304                     215                     215   
28                  305                     216                     216   
29                  306                     123                     123   
30                  307                     233                     233   
31                  308                     124                     124   
32                  309                     203                     203   
33                  310                     216                     216   
34                  311                     124                     124   
35                  312                     150                     150   
36                  313                     174                     174   
37                  314                     241                     241   
38                  315                     242                     242   
39                  316                     268                     268   
40                  317                     189                     189   
41                  318                      24                      24   
42                  319                     229                     229   
43                  320                     124                     124   
44                  321                     226                     226   
45                  322                      44                      44   
46                  323                     124                     124   
47                  324                     245                     245   
48                  325                     124                     124   
49                  326                     156                     156   
50                  327                     211                     211   
51                  328                     246                     246   
52                  329        

In [185]:
# Можем заметить, что STORE_CLOSURE_DTTM у всех магазинов одинаковое, думаю, стоит удалить этот признак
# Также из следующих шагов я заметил, что надо удалить и OPEN тоже, вставил сюда

# Заметим, что в cat_cols попали все столбцы с суффиксом hashing кроме 'STORE_OPEN_DTTM_x' - удалим его
# Это явно время, а не категория
store_location.drop('STORE_CLOSURE_DTTM', axis=1, inplace=True)
store_location.drop('STORE_OPEN_DTTM', axis=1, inplace=True)

In [186]:
# Добавим данные из основного датасета к данным по магазинам
df = df_raw.merge(store_location, left_on='store_location_rk', right_on='STORE_LOCATION_RK')
df.drop('store_location_rk', axis=1, inplace=True)
df.drop('period_start_dt', axis=1, inplace=True)
df

product_rk  demand  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  \
0           40369    29.0          NaN          NaN            NaN   
1           40370    64.0          NaN          NaN            NaN   
2           40372    32.0          NaN          NaN            NaN   
3           40373    10.0          NaN          NaN            NaN   
4           46272    15.0          NaN          NaN            NaN   
...           ...     ...          ...          ...            ...   
35339       40370     NaN          0.0          0.0        1000.00   
35340       40372     NaN          0.0          0.0        2000.00   
35341       40373     NaN          0.0          0.0        3000.00   
35342       46272     NaN          1.0          0.0         284.29   
35343       96212     NaN          1.0          0.0         141.43   

       PRICE_AFTER_DISC  NUM_CONSULTANT  AUTORIZATION_FLAG  day  month  ...  \
0                   NaN             NaN                NaN   19     12  ...   
1                   NaN             NaN                NaN   19     12  ...   
2                   NaN             NaN                NaN   19     12  ...   
3                   NaN             NaN                NaN   19     12  ...   
4                   NaN             NaN                NaN   19     12  ...   
...                 ...             ...                ...  ...    ...  ...   
35339            1000.0             0.0                1.0   30     12  ...   
35340            2000.0             0.0                1.0   30     12  ...   
35341            3000.0             0.0                1.0   30     12  ...   
35342             199.0             0.0                1.0   30     12  ...   
35343              99.0             0.0                1.0   30     12  ...   

        STORE_LOCATION_ATTRIB12_hashing   STORE_LOCATION_ATTRIB13_hashing  \
0      6BA1D912365C006B003750C17E810A8C  6BA1D912365C006B003750C17E810A8C   
1      6BA1D912365C006B003750C17E810A8C  6BA1D912365C006B003750C17E810A8C   
2      6BA1D912365C006B003750C17E810A8C  6BA1D912365C006B003750C17E810A8C   
3      6BA1D912365C006B003750C17E810A8C  6BA1D912365C006B003750C17E810A8C   
4      6BA1D912365C006B003750C17E810A8C  6BA1D912365C006B003750C17E810A8C   
...                                 ...                               ...   
35339  67B1193B31375E3C959BB5246989D0CA  17AC9AE74D16FBC665FFB4CFC2DF24F5   
35340  67B1193B31375E3C959BB5246989D0CA  17AC9AE74D16FBC665FFB4CFC2DF24F5   
35341  67B1193B31375E3C959BB5246989D0CA  17AC9AE74D16FBC665FFB4CFC2DF24F5   
35342  67B1193B31375E3C959BB5246989D0CA  17AC9AE74D16FBC665FFB4CFC2DF24F5   
35343  67B1193B31375E3C959BB5246989D0CA  17AC9AE74D16FBC665FFB4CFC2DF24F5   

        STORE_LOCATION_ATTRIB14_hashing   STORE_LOCATION_ATTRIB15_hashing  \
0      B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
1      B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
2      B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
3      B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
4      B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
...                                 ...                               ...   
35339  B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
35340  B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
35341  B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
35342  B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   
35343  B70EA5F8E1DD1E21F7485AADD433620F  FC5FD090934CE685C1C12E5E0311F1D4   

        STORE_LOCATION_ATTRIB16_hashing   STORE_LOCATION_ATTRIB17_hashing  \
0      3F0DA22658EF921D0F500BFDC5471DB3  FF83472786DB3B25D48ABD61502E1D91   
1      3F0DA22658EF921D0F500BFDC5471DB3  FF83472786DB3B25D48ABD61502E1D91   
2      3F0DA22658EF921D0F500BFDC5471DB3  FF83472786DB3B25D48ABD61502E1D91   
3      3F0DA22658EF921D0F500BFDC5471DB3  FF83472786DB3B25D4

In [187]:
OHE = OneHotEncoder(handle_unknown='ignore')

In [188]:
# Вытащим ID переменных по группам - числовые, категориальные, все кроме ID
# Может пригодиться в дальнейших исследованиях
cat_var = []
num_var = []

for i in range(len(df.dtypes)):
    if df.dtypes[i] == object:
        cat_var.append(df.columns.values[i])
    else:
        num_var.append(df.columns.values[i])

all_var = cat_var + num_var

print('num_cols: ', num_var)
print('')
print('cat_cols: ', cat_var)
print('')
print('all_cols: ', all_var)


num_cols:  ['product_rk', 'demand', 'PROMO1_FLAG', 'PROMO2_FLAG', 'PRICE_REGULAR', 'PRICE_AFTER_DISC', 'NUM_CONSULTANT', 'AUTORIZATION_FLAG', 'day', 'month', 'year', 'weekday', 'weeknum', 'STORE_LOCATION_RK', 'STORE_LOCATION_LVL_RK4', 'STORE_LOCATION_LVL_RK3', 'STORE_LOCATION_LVL_RK2', 'STORE_LOCATION_LVL_RK1']

cat_cols:  ['STORE_LOCATION_ADK_hashing', 'STORE_LOCATION_ATTRIB1_hashing', 'STORE_LOCATION_ATTRIB2_hashing', 'STORE_LOCATION_ATTRIB3_hashing', 'STORE_LOCATION_ATTRIB4_hashing', 'STORE_LOCATION_ATTRIB5_hashing', 'STORE_LOCATION_ATTRIB6_hashing', 'STORE_LOCATION_ATTRIB7_hashing', 'STORE_LOCATION_ATTRIB8_hashing', 'STORE_LOCATION_ATTRIB9_hashing', 'STORE_LOCATION_ATTRIB10_hashing', 'STORE_LOCATION_ATTRIB11_hashing', 'STORE_LOCATION_ATTRIB12_hashing', 'STORE_LOCATION_ATTRIB13_hashing', 'STORE_LOCATION_ATTRIB14_hashing', 'STORE_LOCATION_ATTRIB15_hashing', 'STORE_LOCATION_ATTRIB16_hashing', 'STORE_LOCATION_ATTRIB17_hashing', 'STORE_LOCATION_ATTRIB18_hashing', 'STORE_LOCATION_ATTRIB1

In [189]:
# Где-то здесь кроется ошибка

df_num = df[num_var]
df_cat = OHE.fit_transform(df[cat_var])


index = df_raw.index

df_all = pd.concat((df_num, pd.DataFrame(df_cat.toarray())), axis=1)
df_all.set_index(index, inplace=True)

df_all.columns.values
# df_all.shape

array(['product_rk', 'demand', 'PROMO1_FLAG', 'PROMO2_FLAG',
       'PRICE_REGULAR', 'PRICE_AFTER_DISC', 'NUM_CONSULTANT',
       'AUTORIZATION_FLAG', 'day', 'month', 'year', 'weekday', 'weeknum',
       'STORE_LOCATION_RK', 'STORE_LOCATION_LVL_RK4',
       'STORE_LOCATION_LVL_RK3', 'STORE_LOCATION_LVL_RK2',
       'STORE_LOCATION_LVL_RK1', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12,
       13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29,
       30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45],
      dtype=object)

In [190]:
df_all

product_rk  demand  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  \
0           40369    29.0          NaN          NaN            NaN   
1           40370    64.0          NaN          NaN            NaN   
2           40372    32.0          NaN          NaN            NaN   
3           40373    10.0          NaN          NaN            NaN   
4           46272    15.0          NaN          NaN            NaN   
...           ...     ...          ...          ...            ...   
35537       40370     NaN          0.0          0.0        1000.00   
35538       40372     NaN          0.0          0.0        2000.00   
35539       40373     NaN          0.0          0.0        3000.00   
35540       46272     NaN          1.0          0.0         284.29   
35541       96212     NaN          1.0          0.0         141.43   

       PRICE_AFTER_DISC  NUM_CONSULTANT  AUTORIZATION_FLAG  day  month  ...  \
0                   NaN             NaN                NaN   19     12  ...   
1                   NaN             NaN                NaN   19     12  ...   
2                   NaN             NaN                NaN   19     12  ...   
3                   NaN             NaN                NaN   19     12  ...   
4                   NaN             NaN                NaN   19     12  ...   
...                 ...             ...                ...  ...    ...  ...   
35537            1000.0             0.0                1.0   30     12  ...   
35538            2000.0             0.0                1.0   30     12  ...   
35539            3000.0             0.0                1.0   30     12  ...   
35540             199.0             0.0                1.0   30     12  ...   
35541              99.0             0.0                1.0   30     12  ...   

        36   37   38   39   40   41   42   43   44   45  
0      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
1      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
2      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
3      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
4      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
35537  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35538  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35539  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35540  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35541  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  

[35344 rows x 64 columns]

**Странный момент - в test больше строк, чем в sample_submission, потому что временной отрезок test выходит за рамки sample_submission**

In [191]:
test = pd.read_csv('/Users/alexeysek/Desktop/SAS/HW2_SAS/hw2_test.csv', index_col=0)
test

product_rk  store_location_rk period_start_dt  demand
id                                                          
908         40369                317      02.12.2019     NaN
909         40370                317      02.12.2019     NaN
910         40372                317      02.12.2019     NaN
911         40373                317      02.12.2019     NaN
912         46272                317      02.12.2019     NaN
913         96212                317      02.12.2019     NaN
914         40369                317      09.12.2019     NaN
915         40370                317      09.12.2019     NaN
916         40372                317      09.12.2019     NaN
917         40373                317      09.12.2019     NaN
918         46272                317      09.12.2019     NaN
919         96212                317      09.12.2019     NaN
920         40369                317      16.12.2019     NaN
921         40370                317      16.12.2019     NaN
922         40372                317      16.12.2019     NaN
923         40373                317      16.12.2019     NaN
924         46272                317      16.12.2019     NaN
925         96212                317      16.12.2019     NaN
926         40369                317      23.12.2019     NaN
927         40370                317      23.12.2019     NaN
928         40372                317      23.12.2019     NaN
929         40373                317      23.12.2019     NaN
930         46272                317      23.12.2019     NaN
931         96212                317      23.12.2019     NaN
932         40369                317      30.12.2019     NaN
933         40370                317      30.12.2019     NaN
934         40372                317      30.12.2019     NaN
935         40373                317      30.12.2019     NaN
936         46272                317      30.12.2019     NaN
937         96212                317      30.12.2019     NaN
938         40369                317      06.01.2020     NaN
939         40370                317      06.01.2020     NaN
940         40372                317      06.01.2020     NaN
941         40373                317      06.01.2020     NaN
942         46272                317      06.01.2020     NaN
943         96212                317      06.01.2020     NaN
1837        40369                355      02.12.2019     NaN
1838        40370                355      02.12.2019     NaN
1839        40372                355      02.12.2019     NaN
1840        40373                355      02.12.2019     NaN
1841        46272                355      02.12.2019     NaN
1842        96212                355      02.12.2019     NaN
1843        40369                355      09.12.2019     NaN
1844        40370                355      09.12.2019     NaN
1845        40372                355      09.12.2019     NaN
1846        40373                355      09.12.2019     NaN
1847        46272                355      09.12.2019     NaN
1848        96212                355      09.12.2019     NaN
1849        40369                355      16.12.2019     NaN
1850        40370                355      16.12.2019     NaN
1851        40372                355      16.12.2019     NaN
1852        40373                355      16.12.2019     NaN
1853        46272                355      16.12.2019     NaN
1854        96212                355      16.12.2019     NaN
1855        40369                355      23.12.2019     NaN
1856        40370                355      23.12.2019     NaN
1857        40372                355      23.12.2019     NaN
1858        40373                355      23.12.2019     NaN
1859        46272                355      23.12.2019     NaN
1860        96212                355      23.12.2019     NaN
1861        40369                355      30.12.2019     NaN
1862        40370                355      30.12.2019     NaN
1863        40372                355      30.12.2019     NaN
1864        40373                355      

In [192]:
sample_submission = pd.read_csv('/Users/alexeysek/Downloads/sample_submission.csv', index_col=0)
sample_submission

predicted
id              
908            0
909            0
910            0
911            0
912            0
913            0
914            0
915            0
916            0
917            0
918            0
919            0
920            0
921            0
922            0
923            0
924            0
925            0
926            0
927            0
928            0
929            0
930            0
931            0
932            0
933            0
934            0
935            0
936            0
937            0
1837           0
1838           0
1839           0
1840           0
1841           0
1842           0
1843           0
1844           0
1845           0
1846           0
1847           0
1848           0
1849           0
1850           0
1851           0
1852           0
1853           0
1854           0
1855           0
1856           0
1857           0
1858           0
1859           0
1860           0
1861           0
1862           0
1863           0
1864           0
1865           0
1866           0
2766           0
2767           0
2768           0
2769           0
2770           0
2771           0
2772           0
2773           0
2774           0
2775           0
2776           0
2777           0
2778           0
2779           0
2780           0
2781           0
2782           0
2783           0
2784           0
2785           0
2786           0
2787           0
2788           0
2789           0
2790           0
2791           0
2792           0
2793           0
2794           0
2795           0
3696           0
3697           0
3698           0
3699           0
3700           0
3701           0
3702           0
3703           0
3704           0
3705           0
3706           0
3707           0
3708           0
3709           0
3710           0
3711           0
3712           0
3713           0
3714           0
3715           0
3716           0
3717           0
3718           0
3719           0
3720           0
3721           0
3722           0
3723           0
3724           0
3725           0
4625           0
4626           0
4627           0
4628           0
4629           0
4630           0
4631           0
4632           0
4633           0
4634           0
4635           0
4636           0
4637           0
4638           0
4639           0
4640           0
4641           0
4642           0
4643           0
4644           0
4645           0
4646           0
4647           0
4648           0
4649           0
4650           0
4651           0
4652           0
4653           0
4654           0
5550           0
5551           0
5552           0
5553           0
5554           0
5555           0
5556           0
5557           0
5558           0
5559           0
5560           0
5561           0
5562           0
5563           0
5564           0
5565           0
5566           0
5567           0
5568           0
5569           0
5570           0
5571           0
5572           0
5573           0
5574           0
5575           0
5576           0
5577           0
5578           0
5579           0
6479           0
6480           0
6481           0
6482           0
6483           0
6484           0
6485           0
6486           0
6487           0
6488           0
6489           0
6490           0
6491           0
6492           0
6493           0
6494           0
6495           0
6496           0
6497           0
6498           0
6499           0
6500           0
6501           0
6502           0
6503           0
6504           0
6505           0
6506           0
6507           0
6508           0
7407           0
7408           0
7409           0
7410           0
7411           0
7412           0
7413           0
7414           0
7415           0
7416           0
7417           0
7418           0
7419           0
7420           0
7421           0
7422           0
7423           0
7424           0
7425           0
7426           0
7427           0
7428           0
7429           0
7430        

In [193]:
# Вытащим обучающую выборку (там, где есть значения demand)
train_df = df_all[df_all['demand'].notna()]

train_df

product_rk  demand  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  \
0           40369    29.0          NaN          NaN            NaN   
1           40370    64.0          NaN          NaN            NaN   
2           40372    32.0          NaN          NaN            NaN   
3           40373    10.0          NaN          NaN            NaN   
4           46272    15.0          NaN          NaN            NaN   
...           ...     ...          ...          ...            ...   
35507       40370    24.0          0.0          0.0    1000.000000   
35508       40372    11.0          0.0          0.0    2000.000000   
35509       40373     3.0          0.0          0.0    3000.000000   
35510       46272     0.0          1.0          0.0     284.290000   
35511       96212     2.0          1.0          0.0     121.021429   

       PRICE_AFTER_DISC  NUM_CONSULTANT  AUTORIZATION_FLAG  day  month  ...  \
0                   NaN             NaN                NaN   19     12  ...   
1                   NaN             NaN                NaN   19     12  ...   
2                   NaN             NaN                NaN   19     12  ...   
3                   NaN             NaN                NaN   19     12  ...   
4                   NaN             NaN                NaN   19     12  ...   
...                 ...             ...                ...  ...    ...  ...   
35507       1000.000000             0.0                1.0   25     11  ...   
35508       2000.000000             0.0                1.0   25     11  ...   
35509       3000.000000             0.0                1.0   25     11  ...   
35510        199.000000             0.0                1.0   25     11  ...   
35511         84.714286             0.0                1.0   25     11  ...   

        36   37   38   39   40   41   42   43   44   45  
0      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
1      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
2      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
3      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
4      1.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
35507  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35508  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35509  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35510  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35511  0.0  1.0  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  

[34144 rows x 64 columns]

In [194]:
# Вытащим тестовую выборку
# Идея в том, чтобы просто по индексам из sample_submission вытащить нужные строки))
df_all.drop('weeknum', axis=1, inplace=True)
test_df = df_all.loc[list(sample_submission.index),:]
test_df[['product_rk', 'demand', 'PROMO1_FLAG', 'PROMO2_FLAG',
       'PRICE_REGULAR', 'PRICE_AFTER_DISC', 'NUM_CONSULTANT',
       'AUTORIZATION_FLAG']].fillna(test_df[['product_rk', 'demand', 'PROMO1_FLAG', 'PROMO2_FLAG',
       'PRICE_REGULAR', 'PRICE_AFTER_DISC', 'NUM_CONSULTANT',
       'AUTORIZATION_FLAG']].mean(), inplace=True)
test_df.fillna(0, inplace=True)
test_df

/Users/alexeysek/opt/anaconda3/lib/python3.8/site-packages/pandas/core/series.py:4463: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().fillna(


product_rk  demand  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  \
908         40369     0.0          0.0          0.0     500.000000   
909         40370     0.0          0.0          0.0    1000.000000   
910         40372     0.0          0.0          0.0    2000.000000   
911         40373     0.0          0.0          0.0    3000.000000   
912         46272     0.0          1.0          0.0     284.290000   
913         96212     0.0          1.0          0.0      70.000000   
914         40369     0.0          0.0          0.0     500.000000   
915         40370     0.0          0.0          0.0    1000.000000   
916         40372     0.0          0.0          0.0    2000.000000   
917         40373     0.0          0.0          0.0    3000.000000   
918         46272     0.0          1.0          0.0     284.290000   
919         96212     0.0          1.0          0.0      70.000000   
920         40369     0.0          0.0          0.0     500.000000   
921         40370     0.0          0.0          0.0    1000.000000   
922         40372     0.0          0.0          0.0    2000.000000   
923         40373     0.0          0.0          0.0    3000.000000   
924         46272     0.0          1.0          0.0     284.290000   
925         96212     0.0          1.0          0.0      70.000000   
926         40369     0.0          0.0          0.0     500.000000   
927         40370     0.0          0.0          0.0    1000.000000   
928         40372     0.0          0.0          0.0    2000.000000   
929         40373     0.0          0.0          0.0    3000.000000   
930         46272     0.0          1.0          0.0     284.290000   
931         96212     0.0          1.0          0.0      70.000000   
932         40369     0.0          0.0          0.0     500.000000   
933         40370     0.0          0.0          0.0    1000.000000   
934         40372     0.0          0.0          0.0    2000.000000   
935         40373     0.0          0.0          0.0    3000.000000   
936         46272     0.0          1.0          0.0     284.290000   
937         96212     0.0          1.0          0.0     141.430000   
1837        40369     0.0          0.0          0.0     500.000000   
1838        40370     0.0          0.0          0.0    1000.000000   
1839        40372     0.0          0.0          0.0    2000.000000   
1840        40373     0.0          0.0          0.0    3000.000000   
1841        46272     0.0          1.0          0.0     284.290000   
1842        96212     0.0          1.0          0.0      70.000000   
1843        40369     0.0          0.0          0.0     500.000000   
1844        40370     0.0          0.0          0.0    1000.000000   
1845        40372     0.0          0.0          0.0    2000.000000   
1846        40373     0.0          0.0          0.0    3000.000000   
1847        46272     0.0          1.0          0.0     284.290000   
1848        96212     0.0          1.0          0.0      70.000000   
1849        40369     0.0          0.0          0.0     500.000000   
1850        40370     0.0          0.0          0.0    1000.000000   
1851        40372     0.0          0.0          0.0    2000.000000   
1852        40373     0.0          0.0          0.0    3000.000000   
1853        46272     0.0          1.0          0.0     284.290000   
1854        96212     0.0          1.0          0.0      70.000000   
1855        40369     0.0          0.0          0.0     500.000000   
1856        40370     0.0          0.0          0.0    1000.000000   
1857        40372     0.0          0.0          0.0    2000.000000   
1858        40373     0.0          0.0          0.0    3000.000000   
1859        46272     0.0          1.0          0.0     284.290000   
1860        96212     0.0          1.0          0.0      70.000000   
1861        40369     0.0          0.0          0.0     500.000000   
1862        40370     0.0          0.0          0.0    1000.000000   
1863        40372

In [195]:

train_df.fillna(0, inplace=True)

/Users/alexeysek/opt/anaconda3/lib/python3.8/site-packages/pandas/core/frame.py:4462: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().fillna(


In [196]:
# Сделаем матрицы предикторов и вектор предсказываемой переменной
Y_train = train_df['demand']
X_train = train_df.drop('demand', axis=1)
X_test = test_df.drop('demand', axis=1)

In [197]:
X_train

product_rk  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  PRICE_AFTER_DISC  \
0           40369          0.0          0.0       0.000000          0.000000   
1           40370          0.0          0.0       0.000000          0.000000   
2           40372          0.0          0.0       0.000000          0.000000   
3           40373          0.0          0.0       0.000000          0.000000   
4           46272          0.0          0.0       0.000000          0.000000   
...           ...          ...          ...            ...               ...   
35507       40370          0.0          0.0    1000.000000       1000.000000   
35508       40372          0.0          0.0    2000.000000       2000.000000   
35509       40373          0.0          0.0    3000.000000       3000.000000   
35510       46272          1.0          0.0     284.290000        199.000000   
35511       96212          1.0          0.0     121.021429         84.714286   

       NUM_CONSULTANT  AUTORIZATION_FLAG  day  month  year  ...   36   37  \
0                 0.0                0.0   19     12  2016  ...  1.0  1.0   
1                 0.0                0.0   19     12  2016  ...  1.0  1.0   
2                 0.0                0.0   19     12  2016  ...  1.0  1.0   
3                 0.0                0.0   19     12  2016  ...  1.0  1.0   
4                 0.0                0.0   19     12  2016  ...  1.0  1.0   
...               ...                ...  ...    ...   ...  ...  ...  ...   
35507             0.0                1.0   25     11  2019  ...  0.0  1.0   
35508             0.0                1.0   25     11  2019  ...  0.0  1.0   
35509             0.0                1.0   25     11  2019  ...  0.0  1.0   
35510             0.0                1.0   25     11  2019  ...  0.0  1.0   
35511             0.0                1.0   25     11  2019  ...  0.0  1.0   

        38   39   40   41   42   43   44   45  
0      0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
1      0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
2      0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
3      0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
4      0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
...    ...  ...  ...  ...  ...  ...  ...  ...  
35507  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35508  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35509  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35510  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  
35511  0.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  

[34144 rows x 63 columns]

In [198]:
X_test

product_rk  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  PRICE_AFTER_DISC  \
908         40369          0.0          0.0     500.000000        500.000000   
909         40370          0.0          0.0    1000.000000       1000.000000   
910         40372          0.0          0.0    2000.000000       2000.000000   
911         40373          0.0          0.0    3000.000000       3000.000000   
912         46272          1.0          0.0     284.290000        199.000000   
913         96212          1.0          0.0      70.000000         49.000000   
914         40369          0.0          0.0     500.000000        500.000000   
915         40370          0.0          0.0    1000.000000       1000.000000   
916         40372          0.0          0.0    2000.000000       2000.000000   
917         40373          0.0          0.0    3000.000000       3000.000000   
918         46272          1.0          0.0     284.290000        199.000000   
919         96212          1.0          0.0      70.000000         49.000000   
920         40369          0.0          0.0     500.000000        500.000000   
921         40370          0.0          0.0    1000.000000       1000.000000   
922         40372          0.0          0.0    2000.000000       2000.000000   
923         40373          0.0          0.0    3000.000000       3000.000000   
924         46272          1.0          0.0     284.290000        199.000000   
925         96212          1.0          0.0      70.000000         49.000000   
926         40369          0.0          0.0     500.000000        500.000000   
927         40370          0.0          0.0    1000.000000       1000.000000   
928         40372          0.0          0.0    2000.000000       2000.000000   
929         40373          0.0          0.0    3000.000000       3000.000000   
930         46272          1.0          0.0     284.290000        199.000000   
931         96212          1.0          0.0      70.000000         49.000000   
932         40369          0.0          0.0     500.000000        500.000000   
933         40370          0.0          0.0    1000.000000       1000.000000   
934         40372          0.0          0.0    2000.000000       2000.000000   
935         40373          0.0          0.0    3000.000000       3000.000000   
936         46272          1.0          0.0     284.290000        161.096667   
937         96212          1.0          0.0     141.430000         99.000000   
1837        40369          0.0          0.0     500.000000        500.000000   
1838        40370          0.0          0.0    1000.000000       1000.000000   
1839        40372          0.0          0.0    2000.000000       2000.000000   
1840        40373          0.0          0.0    3000.000000       3000.000000   
1841        46272          1.0          0.0     284.290000        199.000000   
1842        96212          1.0          0.0      70.000000         49.000000   
1843        40369          0.0          0.0     500.000000        500.000000   
1844        40370          0.0          0.0    1000.000000       1000.000000   
1845        40372          0.0          0.0    2000.000000       2000.000000   
1846        40373          0.0          0.0    3000.000000       3000.000000   
1847        46272          1.0          0.0     284.290000        199.000000   
1848        96212          1.0          0.0      70.000000         49.000000   
1849        40369          0.0          0.0     500.000000        500.000000   
1850        40370          0.0          0.0    1000.000000       1000.000000   
1851        40372          0.0          0.0    2000.000000       2000.000000   
1852        40373          0.0          0.0    3000.000000       3000.000000   
1853        46272          1.0          0.0     284.290000        199.000000   
1854        96212          1.0          0.0      70.000000         49.000000   
1855        40369          0.0          0.0     500.000000        500.000000   
1856   

# Вспомнил, в чем была ошибка - тип столбца weeknum UInt32 не давал модели обучиться, поэтому я просто выкинул эту переменную

'+ заполнял пропуски в трейне нулями

In [199]:
pd.options.display.max_rows = 4000
X_train.dtypes

product_rk                  int64
PROMO1_FLAG               float64
PROMO2_FLAG               float64
PRICE_REGULAR             float64
PRICE_AFTER_DISC          float64
NUM_CONSULTANT            float64
AUTORIZATION_FLAG         float64
day                         int64
month                       int64
year                        int64
weekday                     int64
weeknum                    UInt32
STORE_LOCATION_RK           int64
STORE_LOCATION_LVL_RK4      int64
STORE_LOCATION_LVL_RK3      int64
STORE_LOCATION_LVL_RK2      int64
STORE_LOCATION_LVL_RK1      int64
0                         float64
1                         float64
2                         float64
3                         float64
4                         float64
5                         float64
6                         float64
7                         float64
8                         float64
9                         float64
10                        float64
11                        float64
12            

In [200]:
X_train.drop('weeknum', axis=1, inplace=True)

## Часть 2. Построение моделей

In [201]:
# Найдем оптимальные гиперпараметры кросс-валидацией

from sklearn.model_selection import RandomizedSearchCV
# Выберем некоторые параметры для кросс-валидации
grid_params = {
'boosting_type' : ['gbdt', 'dart', 'goss', 'rf'],
'num_leaves': np.arange(50,300,50),
'learning_rate': np.linspace(0.05,0.25,5),
'n_estimators': np.arange(100,500,100)
}

model = lgb.LGBMRegressor(n_jobs=-1, metric='mae')

# Используем все ядра для кросс-валидации, скоринг - как в задаче, verbose, чтобы видеть прогресс
grid = RandomizedSearchCV(model, grid_params, n_iter=100, scoring='roc_auc', n_jobs=-1, verbose=2, cv=2)
grid.fit(X_train, Y_train)
grid.best_params_

Fitting 2 folds for each of 100 candidates, totalling 200 fits


/Users/alexeysek/opt/anaconda3/lib/python3.8/site-packages/sklearn/model_selection/_search.py:922: UserWarning: One or more of the test scores are non-finite: [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan]
  warnings.warn(


{'num_leaves': 100,
 'n_estimators': 300,
 'learning_rate': 0.05,
 'boosting_type': 'gbdt'}

In [202]:
# Зафитим модель c оптимальными гиперпараметрами и сделаем прогноз
lgb_params = {}
lgb_params['n_jobs'] = -1 # чтобы использовались все ядра
lgb_params['boosting_type'] = 'goss'
lgb_params['num_leaves'] = 100
lgb_params['learning_rate'] = 0.025
lgb_params['n_estimators'] = 400 # из кросс-валидации
lgb_params['metric'] = 'mae' # из кросс-валидации


lgb_train_set = lgb.Dataset(X_train, Y_train)
estimator = lgb.train(lgb_params, lgb_train_set, num_boost_round=30)
Y_pred = estimator.predict(X_test)
Y_pred

/Users/alexeysek/opt/anaconda3/lib/python3.8/site-packages/lightgbm/engine.py:151: UserWarning: Found `n_estimators` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002954 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 599
[LightGBM] [Info] Number of data points in the train set: 34144, number of used features: 45
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 12.245636


array([12.44376006, 15.01578125,  7.72258215, ..., 30.29471691,
        9.56797982, 16.99643068])

In [203]:
Y_pred.shape

(1200,)

In [204]:
# Приведем данные в нужный вид
submission_SEK = pd.DataFrame()
submission_SEK['id'] = list(sample_submission.index)
submission_SEK['predicted'] = Y_pred
# submission_SEK.set_index(sample_submission.index, inplace=True)
submission_SEK

id   predicted
0       908   12.443760
1       909   15.015781
2       910    7.722582
3       911    5.235716
4       912    2.955725
5       913    3.872653
6       914   11.546742
7       915   13.893641
8       916    5.394113
9       917    4.227870
10      918    2.273207
11      919    3.986474
12      920   13.924426
13      921   15.419609
14      922    5.857033
15      923    4.566776
16      924    2.953799
17      925    4.304197
18      926   29.726953
19      927   42.106364
20      928   10.994592
21      929    7.619555
22      930    3.779622
23      931    6.148981
24      932   49.674461
25      933   56.096712
26      934   18.840176
27      935   12.747765
28      936    8.519309
29      937    9.962689
30     1837   15.150644
31     1838   20.185392
32     1839   13.418314
33     1840    9.967453
34     1841    7.840549
35     1842    8.707823
36     1843   12.568605
37     1844   18.640453
38     1845   10.878046
39     1846    8.764776
40     1847    6.524656
41     1848    7.968220
42     1849   14.767124
43     1850   19.325755
44     1851   10.238183
45     1852    8.283912
46     1853    7.087763
47     1854    8.955106
48     1855   33.087706
49     1856   50.642676
50     1857   31.390369
51     1858   23.048284
52     1859    8.816950
53     1860    9.571729
54     1861   60.704234
55     1862   71.209139
56     1863   39.566757
57     1864   29.361403
58     1865   15.155622
59     1866   15.064821
60     2766   16.206330
61     2767   18.898919
62     2768   11.196334
63     2769    7.708043
64     2770    4.805158
65     2771    3.409163
66     2772   16.481125
67     2773   19.726766
68     2774    9.878316
69     2775    7.015455
70     2776    3.858397
71     2777    2.763954
72     2778   20.421734
73     2779   23.536026
74     2780   11.752332
75     2781    8.205094
76     2782    4.922746
77     2783    3.532391
78     2784   39.491759
79     2785   54.367794
80     2786   27.569373
81     2787   18.631215
82     2788    6.192590
83     2789   13.939251
84     2790   54.564026
85     2791   62.203723
86     2792   34.516137
87     2793   25.347893
88     2794   11.313589
89     2795   20.131942
90     3696   21.569953
91     3697   24.533701
92     3698   13.068710
93     3699    8.494429
94     3700    5.249729
95     3701    4.559588
96     3702   20.685120
97     3703   23.651983
98     3704   12.049022
99     3705    7.979405
100    3706    4.467237
101    3707    4.169988
102    3708   24.953226
103    3709   26.459029
104    3710   12.649272
105    3711    8.392764
106    3712    4.981304
107    3713    4.391433
108    3714   53.995835
109    3715   68.811902
110    3716   32.140596
111    3717   19.211220
112    3718    6.360386
113    3719    4.184476
114    3720   67.485097
115    3721   75.184990
116    3722   40.493731
117    3723   26.476713
118    3724   11.342592
119    3725   11.796655
120    4625   12.157493
121    4626   14.330465
122    4627    9.307938
123    4628    7.398356
124    4629    4.327447
125    4630    6.173220
126    4631   11.229112
127    4632   13.744396
128    4633    7.361394
129    4634    6.964855
130    4635    4.070144
131    4636    7.088364
132    4637   13.954624
133    4638   15.472502
134    4639    7.398845
135    4640    7.277412
136    4641    4.710992
137    4642    7.814335
138    4643   35.177185
139    4644   50.281362
140    4645   26.176126
141    4646   18.248980
142    4647    7.071725
143    4648    9.403787
144    4649   55.402572
145    4650   62.251555
146    4651   35.374448
147    4652   25.414419
148    4653   13.300475
149    4654   24.670377
150    5550    4.306260
151    5551    7.662130
152    5552    5.223812
153    5553    3.832828
154    5554    1.682705
155    5555    5.076384
156    5556    3.407741
157    5557    6.801700
158    5558    4.443306
159    5559    3.673947
160    5560    1.840622
161    5561    6.044999
162    5562    3.964780
163    5563    7.113641
164    5564    4.675245
165    5565    4.154465
1

In [205]:
# Экспортируем результат в csv
submission_SEK.to_csv('/Users/alexeysek/Desktop/Solution_SEK.csv', index=False)

### я пытался строить еще random forest и sgd, но получилось не очень, поэтому удалил неудачные попытки)